Fake news classifier using Bi-LSTM

In [1]:
import pandas as pd

In [2]:
df = pd.read_csv("/kaggle/input/fake-news-classification/WELFake_Dataset.csv")


In [3]:
df.head()

Unnamed: 0                                              title  \
0           0  LAW ENFORCEMENT ON HIGH ALERT Following Threat...   
1           1                                                NaN   
2           2  UNBELIEVABLE! OBAMA’S ATTORNEY GENERAL SAYS MO...   
3           3  Bobby Jindal, raised Hindu, uses story of Chri...   
4           4  SATAN 2: Russia unvelis an image of its terrif...   

                                                text  label  
0  No comment is expected from Barack Obama Membe...      1  
1     Did they post their votes for Hillary already?      1  
2   Now, most of the demonstrators gathered last ...      1  
3  A dozen politically active pastors came here f...      0  
4  The RS-28 Sarmat missile, dubbed Satan 2, will...      1

In [4]:
df.drop("Unnamed: 0",axis=1,inplace=True)

In [5]:
df.isnull().sum()

title    558
text      39
label      0
dtype: int64

In [6]:
df.shape

(72134, 3)

In [7]:
df=df.dropna()

In [8]:
df.head()

title  \
0  LAW ENFORCEMENT ON HIGH ALERT Following Threat...   
2  UNBELIEVABLE! OBAMA’S ATTORNEY GENERAL SAYS MO...   
3  Bobby Jindal, raised Hindu, uses story of Chri...   
4  SATAN 2: Russia unvelis an image of its terrif...   
5  About Time! Christian Group Sues Amazon and SP...   

                                                text  label  
0  No comment is expected from Barack Obama Membe...      1  
2   Now, most of the demonstrators gathered last ...      1  
3  A dozen politically active pastors came here f...      0  
4  The RS-28 Sarmat missile, dubbed Satan 2, will...      1  
5  All we can say on this one is it s about time ...      1

In [9]:
# Get independent features
x=df.drop('label', axis=1)

In [10]:
y=df['label']

In [11]:
# check whether dataset is balanced or not
y.value_counts()

label
1    36509
0    35028
Name: count, dtype: int64

In [1]:
import sys
print(sys.executable)


c:\Users\sawan\python.exe


In [1]:
import tensorflow as tf

In [1]:
tf.__version__

NameError: name 'tf' is not defined

In [14]:
from tensorflow.keras.layers import Embedding
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.preprocessing.text import one_hot
from tensorflow.keras.layers import LSTM
from tensorflow.keras.layers import Dense , Bidirectional , Input


In [15]:
voc_size=1000

In [16]:
messages=x.copy()

In [17]:
messages=messages.reset_index()

In [18]:
messages.drop('index' , axis=1 , inplace=True)

In [19]:
messages

title  \
0      LAW ENFORCEMENT ON HIGH ALERT Following Threat...   
1      UNBELIEVABLE! OBAMA’S ATTORNEY GENERAL SAYS MO...   
2      Bobby Jindal, raised Hindu, uses story of Chri...   
3      SATAN 2: Russia unvelis an image of its terrif...   
4      About Time! Christian Group Sues Amazon and SP...   
...                                                  ...   
71532  Russians steal research on Trump in hack of U....   
71533   WATCH: Giuliani Demands That Democrats Apolog...   
71534  Migrants Refuse To Leave Train At Refugee Camp...   
71535  Trump tussle gives unpopular Mexican leader mu...   
71536  Goldman Sachs Endorses Hillary Clinton For Pre...   

                                                    text  
0      No comment is expected from Barack Obama Membe...  
1       Now, most of the demonstrators gathered last ...  
2      A dozen politically active pastors came here f...  
3      The RS-28 Sarmat missile, dubbed Satan 2, will...  
4      All we can say on this one is it s about time ...  
...                                                  ...  
71532  WASHINGTON (Reuters) - Hackers believed to be ...  
71533  You know, because in fantasyland Republicans n...  
71534  Migrants Refuse To Leave Train At Refugee Camp...  
71535  MEXICO CITY (Reuters) - Donald Trump’s combati...  
71536  Goldman Sachs Endorses Hillary Clinton For Pre...  

[71537 rows x 2 columns]

In [20]:
import nltk

In [21]:
import re
from nltk.corpus import stopwords
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /usr/share/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [22]:
# Dataset preperocessing
# porter stemmer
from nltk.stem.porter import PorterStemmer


In [23]:
ps=PorterStemmer()
corpus=[]
for i in range (0 , len(messages)):
  print(i)
  review=re.sub('[^a-zA-Z]',' ',messages['title'][i])
  review=review.lower()
  review=review.split()

  review=[ps.stem(word) for word in review if not word in stopwords.words('english')]
  review=' '.join(review)
  corpus.append(review)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
275
276
27

In [24]:
corpus

['law enforc high alert follow threat cop white blacklivesmatt fyf terrorist video',
 'unbeliev obama attorney gener say charlott rioter peac protest home state north carolina video',
 'bobbi jindal rais hindu use stori christian convers woo evangel potenti bid',
 'satan russia unv imag terrifi new supernuk western world take notic',
 'time christian group sue amazon splc design hate group',
 'dr ben carson target ir never audit spoke nation prayer breakfast',
 'hous intel chair trump russia fake stori evid anyth video',
 'sport bar owner ban nfl game show true american sport like speak rural america video',
 'latest pipelin leak underscor danger dakota access pipelin',
 'gop senat smack punchabl alt right nazi internet',
 'may brexit offer would hurt cost eu citizen eu parliament',
 'schumer call trump appoint offici overse puerto rico relief',
 'watch hilari ad call question health age clinton crime famili boss',
 'chang expect espn polit agenda despit huge subscrib declin breitbart'

In [25]:
onehot_repr=[one_hot(words, voc_size) for words in corpus]
print(onehot_repr)

[[555, 391, 189, 197, 566, 547, 200, 892, 791, 632, 336, 570], [844, 195, 47, 109, 839, 881, 68, 197, 168, 199, 538, 34, 127, 570], [835, 373, 106, 348, 261, 413, 601, 185, 238, 478, 254, 346], [542, 608, 621, 271, 942, 79, 380, 804, 679, 930, 24], [12, 601, 678, 209, 555, 625, 149, 469, 678], [293, 565, 104, 447, 247, 680, 473, 406, 586, 630, 164], [930, 748, 831, 555, 608, 470, 413, 144, 169, 570], [65, 988, 880, 632, 360, 398, 387, 766, 667, 65, 327, 62, 341, 709, 570], [266, 811, 683, 980, 436, 663, 817, 811], [115, 149, 684, 757, 501, 142, 439, 257], [469, 758, 370, 670, 552, 272, 858, 449, 858, 517], [410, 475, 555, 174, 975, 68, 582, 950, 299], [726, 798, 55, 475, 274, 702, 292, 400, 63, 624, 270], [902, 20, 567, 506, 146, 966, 646, 971, 207, 129], [705, 744, 207, 656, 90, 930, 48], [553, 992, 885, 176, 80, 273, 22, 2, 197], [636, 681, 273, 781, 492, 684, 988, 332], [239, 216, 679, 240, 988, 640, 746, 555, 108, 618, 248, 542, 861, 852], [847, 718, 839, 400, 164, 774, 469, 297, 9

# Embedding representation

In [26]:
len(max(corpus))

49

In [27]:
sent_length=49

In [28]:
embedded_docs=pad_sequences(onehot_repr, padding='pre', maxlen=sent_length)

In [29]:
embedded_docs

array([[  0,   0,   0, ..., 632, 336, 570],
       [  0,   0,   0, ...,  34, 127, 570],
       [  0,   0,   0, ..., 478, 254, 346],
       ...,
       [  0,   0,   0, ...,  70, 834, 711],
       [  0,   0,   0, ...,  40, 936, 997],
       [  0,   0,   0, ..., 198, 400, 746]], dtype=int32)

In [30]:
embedded_docs.shape

(71537, 49)

# Creating the model

In [31]:
embedding_vector_features=40
model=Sequential()
model.add(Input(shape=(sent_length, )))
model.add(Embedding(voc_size , embedding_vector_features))
model.add(Bidirectional(LSTM(100)))
model.add(Dense(1, activation='sigmoid'))
model.compile(loss='binary_crossentropy', optimizer='adam' , metrics=['accuracy'])
print(model.summary())

I0000 00:00:1762521583.824508      37 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 13942 MB memory:  -> device: 0, name: Tesla T4, pci bus id: 0000:00:04.0, compute capability: 7.5
I0000 00:00:1762521583.825161      37 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:1 with 13942 MB memory:  -> device: 1, name: Tesla T4, pci bus id: 0000:00:05.0, compute capability: 7.5


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ embedding (Embedding)           │ (None, 49, 40)         │        40,000 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bidirectional (Bidirectional)   │ (None, 200)            │       112,800 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dense (Dense)                   │ (None, 1)              │           201 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 153,001 (597.66 KB)

 Trainable params: 153,001 (597.66 KB)

 Non-trainable params: 0 (0.00 B)

None


In [32]:
import numpy as np
x_final=np.array(embedded_docs)
y_final=np.array(y)

In [33]:
from sklearn.model_selection import train_test_split
xtrain , xtest , ytrain ,ytest= train_test_split(x_final , y_final , test_size=0.3 , random_state=33)

In [48]:
# Model training
model.fit(xtrain , ytrain, validation_data=(xtest, ytest), epochs=20 , batch_size=32)

Epoch 1/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9288 - loss: 0.1657 - val_accuracy: 0.8680 - val_loss: 0.3736
Epoch 2/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9359 - loss: 0.1503 - val_accuracy: 0.8678 - val_loss: 0.3860
Epoch 3/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9411 - loss: 0.1383 - val_accuracy: 0.8689 - val_loss: 0.4094
Epoch 4/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9467 - loss: 0.1262 - val_accuracy: 0.8664 - val_loss: 0.4236
Epoch 5/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9512 - loss: 0.1140 - val_accuracy: 0.8648 - val_loss: 0.4772
Epoch 6/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9598 - loss: 0.0982 - val_accuracy: 0.8682 - val_loss: 0.5261
Epoch 7/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9656 - loss: 0.0861 - val_accuracy: 0.8648 - val_loss: 0.5551
Epoch 8/20
1565/1565 ━━━━━━━━━━━━━━━━━━━━ 14s 9ms/step - accuracy: 0.9718 - loss: 0

In [ ]:
import pickle
pickle.dump(model, open('Bi-lstm-fakenews.pkl', 'wb'))


In [36]:
ypred=model.predic(xtest)

671/671 ━━━━━━━━━━━━━━━━━━━━ 2s 3ms/step


In [41]:
ypred=np.where(ypred>=0.5,1,0)

In [46]:
from sklearn.metrics import confusion_matrix , accuracy_score

In [44]:
confusion_matrix(ytest, ypred)

array([[8709, 1860],
       [ 969, 9924]])

In [47]:

print(accuracy_score(ytest , ypred))

0.8681856304165502
